<h1>Coursera Final Capstone</h1><h2>Finding best spot for Automobile Exhibition</h2>

### Importing Libraries

In [22]:
import numpy as np # library to handle data in a vectorized manner
import time

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
import geocoder
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
from opencage.geocoder import OpenCageGeocode

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

from bs4 import BeautifulSoup
from googlesearch import search
import urllib

print('Libraries imported.')

Libraries imported.


### 2. Download and Explore Dataset

### Creating DataFrame for Postal codes of Various Cities

In [2]:
Pincode_links = ["https://www.mapsofindia.com/pincode/india/maharashtra/mumbai/", \
                "https://www.mapsofindia.com/pincode/india/delhi/central-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/east-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/new-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/north-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/north-west-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/south-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/south-west-delhi/", \
                "https://www.mapsofindia.com/pincode/india/delhi/west-delhi/", \
                "https://www.mapsofindia.com/pincode/india/gujarat/ahmedabad/", \
                "https://www.mapsofindia.com/pincode/india/karnataka/bangalore/", \
                "https://www.mapsofindia.com/pincode/india/telangana/hyderabad/", \
                "https://www.mapsofindia.com/pincode/india/west-bengal/kolkata/"]

headers = {'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:52.0) Gecko/20100101 Firefox/52.0'}

In [3]:
column_name = ['Area','Pincode','State','District']
column_data = []

for link in Pincode_links:
    req = requests.get(link, headers = headers)

    soup = BeautifulSoup(req.text, 'html')

    soup_details = soup.find_all('tr')
    
    for i in soup_details[2:]:
        row = []
        for td in i.find_all('td'):
            row.append(td.text.replace('\n',' ').strip())
        column_data.append(row)
    
    Pincode_df = pd.DataFrame(column_data, columns=column_name)

Pincode_df.head()

Area Pincode        State District
0  A I staff colony  400029  Maharashtra   Mumbai
1  Aareymilk Colony  400065  Maharashtra   Mumbai
2          Agripada  400011  Maharashtra   Mumbai
3           Airport  400099  Maharashtra   Mumbai
4          Ambewadi  400004  Maharashtra   Mumbai

In [4]:
Pincode_df.dropna(axis = 0, inplace = True)

#Pincode_df.to_excel("Pincode.xlsx")

print(Pincode_df.shape)

(1913, 4)


### Getting Lat and Long

latlong_data = []

key = 'your API key'
geocoder = OpenCageGeocode(key)

for i in range(len(Pincode_df)):
    row = []
    query = u'{}, {}, {}'.format(Pincode_df.iloc[i,0], Pincode_df.iloc[i,3], Pincode_df.iloc[i,1])
    try:
        results = geocoder.geocode(query)
    
        row.append(results[0]['geometry']['lat']) 
        row.append(results[0]['geometry']['lng'])
    except:
        row.append(np.nan)
        row.append(np.nan)
    
    latlong_data.append(row)

In [5]:
latlong_data = pd.read_excel("Latlong_data.xlsx")
print('File Downloaded!')

File Downloaded!


In [6]:
Latlong_df = pd.DataFrame(latlong_data, columns=['Latitude', 'Longitude'])
Latlong_df.head()

Latitude  Longitude
0  18.986000  72.825900
1  19.169900  72.850400
2  18.975302  72.824898
3  19.105137  72.855803
4  19.186776  72.859313

In [7]:
Area_Loc_df = Pincode_df
Area_Loc_df = Area_Loc_df.assign(Latitude = Latlong_df['Latitude'], Longitude = Latlong_df['Longitude'])

Area_Loc_df = Area_Loc_df[['Area', 'District', 'State', 'Pincode', 'Latitude', 'Longitude']]

print(Area_Loc_df.shape)
Area_Loc_df.head()

(1913, 6)


Area District        State Pincode   Latitude  Longitude
0  A I staff colony   Mumbai  Maharashtra  400029  18.986000  72.825900
1  Aareymilk Colony   Mumbai  Maharashtra  400065  19.169900  72.850400
2          Agripada   Mumbai  Maharashtra  400011  18.975302  72.824898
3           Airport   Mumbai  Maharashtra  400099  19.105137  72.855803
4          Ambewadi   Mumbai  Maharashtra  400004  19.186776  72.859313

Small Summary of Final DataFrame

In [8]:
print('The dataframe has {} Districts and {} Locations.'.format(len(Area_Loc_df['District'].unique()),Area_Loc_df.shape[0]))

The dataframe has 13 Districts and 1913 Locations.


In [9]:
address = ['Mumbai', 'Delhi', 'Bangalore', 'Ahmedabad', 'Hyderabad', 'Kolkata']
district_data = []

key = '797a56e6eb604ec8bf7e917ecc75067b'
geocoder = OpenCageGeocode(key)

for place in address:
    row = []
    p = u'{}, India'.format(place)
    results = geocoder.geocode(p)
    row.append(place)
    row.append(results[0]['geometry']['lat'])
    row.append(results[0]['geometry']['lng'])

    district_data.append(row)

District_df = pd.DataFrame(district_data, columns= ['District', 'Latitude', 'Longitude'])

District_df

District   Latitude  Longitude
0     Mumbai  19.075990  72.877393
1      Delhi  28.651718  77.221939
2  Bangalore  12.979120  77.591300
3  Ahmedabad  23.021624  72.579707
4  Hyderabad  17.388786  78.461065
5    Kolkata  22.572672  88.363882

### Use geopy library to get the latitude and longitude values of India.

#### In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent ny_explorer, as shown below.

In [10]:
address = u'India'
results = geocoder.geocode(address)

latitude = results[0]['geometry']['lat']
longitude = results[0]['geometry']['lng']

print('The geograpical coordinate of India are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of India are 22.3511148, 78.6677428.


### Create a map of India with District superimposed on top.

In [11]:
# create map of New York using latitude and longitude values
map_india = folium.Map(location=[latitude, longitude], zoom_start=5)

# add markers to map
for lat, lng, district in zip(District_df['Latitude'], District_df['Longitude'], District_df['District']):
    label = '{}, India'.format(district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_india)  
    
map_india

### Segregating Data based on District

In [81]:
Mumbai_df = Area_Loc_df[Area_Loc_df['District'] == 'Mumbai']
print("Shape of {} is {}".format('Mumbai_df',Mumbai_df.shape))

Delhi_df = Area_Loc_df[Area_Loc_df['District'].str.contains('Delhi|delhi', regex = True)].reset_index(drop = True)
print("Shape of {} is {}".format('Delhi_df',Delhi_df.shape))

Bangalore_df = Area_Loc_df[Area_Loc_df['District'] == 'Bangalore']
print("Shape of {} is {}".format('Bangalore_df',Bangalore_df.shape))

Ahmedabad_df = Area_Loc_df[Area_Loc_df['District'] == 'Ahmedabad']
print("Shape of {} is {}".format('Ahmedabad_df',Ahmedabad_df.shape))

Hyderabad_df = Area_Loc_df[Area_Loc_df['District'] == 'Hyderabad']
print("Shape of {} is {}".format('Hyderabad_df',Hyderabad_df.shape))

Kolkata_df = Area_Loc_df[Area_Loc_df['District'] == 'Kolkata']
print("Shape of {} is {}".format('Kolkata_df',Kolkata_df.shape))

print("Shape of {} is {}".format('Area_Loc_df',Area_Loc_df.shape))

Shape of Mumbai_df is (182, 6)
Shape of Delhi_df is (530, 6)
Shape of Bangalore_df is (294, 6)
Shape of Ahmedabad_df is (501, 6)
Shape of Hyderabad_df is (228, 6)
Shape of Kolkata_df is (178, 6)
Shape of Area_Loc_df is (1913, 6)


### Creating a Map based on Districts

#### For Mumbai District

In [82]:
# create map of New York using latitude and longitude values
map_mumbai = folium.Map(location=[District_df.iloc[0,1], District_df.iloc[0,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Mumbai_df['Latitude'], Mumbai_df['Longitude'], Mumbai_df['District'], Mumbai_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_mumbai)  
    
map_mumbai

#### For Delhi District

In [83]:
# create map of New York using latitude and longitude values
map_delhi = folium.Map(location=[District_df.iloc[1,1], District_df.iloc[1,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Delhi_df['Latitude'], Delhi_df['Longitude'], Delhi_df['District'], Delhi_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_delhi)  
    
map_delhi

In [84]:
# create map of New York using latitude and longitude values
map_bangalore = folium.Map(location=[District_df.iloc[2,1], District_df.iloc[2,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Bangalore_df['Latitude'], Bangalore_df['Longitude'], Bangalore_df['District'], Bangalore_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bangalore)  
    
map_bangalore

In [85]:
# create map of New York using latitude and longitude values
map_ahmedabad = folium.Map(location=[District_df.iloc[3,1], District_df.iloc[3,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Ahmedabad_df['Latitude'], Ahmedabad_df['Longitude'], Ahmedabad_df['District'], Ahmedabad_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_ahmedabad)  
    
map_ahmedabad

In [86]:
# create map of New York using latitude and longitude values
map_hyderabad = folium.Map(location=[District_df.iloc[4,1], District_df.iloc[4,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Hyderabad_df['Latitude'], Hyderabad_df['Longitude'], Hyderabad_df['District'], Hyderabad_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_hyderabad)  
    
map_hyderabad

In [87]:
# create map of New York using latitude and longitude values
map_kolkata = folium.Map(location=[District_df.iloc[5,1], District_df.iloc[5,2]], zoom_start=11)

# add markers to map
for lat, lng, district, area in zip(Kolkata_df['Latitude'], Kolkata_df['Longitude'], Kolkata_df['District'], Kolkata_df['Area']):
    label = '{}, {}, India'.format(area, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_kolkata)  
    
map_kolkata

### Define Foursquare Credentials and Version

In [109]:
CLIENT_ID = 'Z20BNBFMFB2M4IBIQXJ1QPF52XGQETRJCNWLNUAD4HVTBAMN' # your Foursquare ID
CLIENT_SECRET = 'XYCM3FKKVVIFUVSFEDCZMQU2RLMXS2MFLJHM2BCQV3EU3CID' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: Z20BNBFMFB2M4IBIQXJ1QPF52XGQETRJCNWLNUAD4HVTBAMN
CLIENT_SECRET:XYCM3FKKVVIFUVSFEDCZMQU2RLMXS2MFLJHM2BCQV3EU3CID


## 2. Explore Places in Each District.

In [95]:
reject_list = []

def getNearbyVenues(places, districts, pincode, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for place, district, pincode, lat, lng in zip(places, districts, pincode, latitudes, longitudes):
        print(place)
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        try:
            results = requests.get(url).json()["response"]['groups'][0]['items']
            
            if len(results) > 0:
                # return only relevant information for each nearby venue
                venues_list.append([(place, 
                                    district, 
                                    lat, 
                                    lng, 
                                    v['venue']['name'], 
                                    v['venue']['location']['lat'], 
                                    v['venue']['location']['lng'], 
                                    v['venue']['categories'][0]['name']) for v in results])
            else:
                reject_list.append(pincode)
        except:
            reject_list.append(pincode)

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Area', 
                             'District',
                             'Area Latitude', 
                             'Area Longitude', 
                             'Venue', 
                             'Venue Latitude', 
                             'Venue Longitude', 
                             'Venue Category']
    
    return(nearby_venues)

In [114]:
# type your answer here
Kolkata_venues_df  = getNearbyVenues(places=Kolkata_df['Area'], districts=Kolkata_df['District'], pincode=Kolkata_df['Pincode'], latitudes=Kolkata_df['Latitude'], longitudes=Kolkata_df['Longitude'])
print(Kolkata_venues_df.shape)
print(len(reject_list))

A.J.c.bose road
Abinash Chaowdhury lane
Alipore
Alipore Bodyguard line
Alipore Civil court
Alipore Dist board
Asylum Lane
Badartala
Baghajatin
Bakery Road
Ballygunge
Ballygunge Rs
Ballygunge Sc college
Bamboovila
Barabazar
Barisha
Bartala
Behala
Behala Municipal market
Beleghata
Bengal Chemical
Bhawanipore
Bidhangarh
Bijoygarh
Bosepukur Road
Bowbazar
Brace Bridge
Brahma Samaj road
Chetla
Chittaranjan Avenue
Circus Avenue
Cmda Abasan
College Square
Colootola
Council House street
Customs House
Daulatpur
Dhakuria
Dharmatala
Dover Lane
E.K.t
Elliot Road
Esplanade
Fort William
Ganguly Bagan
Garcha Road
Garden Reach
Garfa
Garia Bt
Gariahat Market
Gobinda Khatick road
Gokhel Road
Golf Green
Golpark
Great Eastern hotel
Haltu
Haridevpur
Hastings
Hindustan Building
Hyde Road
Income Tax building
Indrani Park
Intally
Jadavgarh
Jadavpur University
Jairampur
Jayshree Park
Jhowtala
Jodhpur Park
Joramandir
K.C.mills
K.G bose sarani
K.M.hospital
K.P.bazar
K.P.roy lane
Kalabagan
Kalagachia
Kalighat
Kali

In [115]:
#Kolkata_rejected_list = reject_list

In [127]:
#Mumbai_venues_df.to_excel("Mumbai_venues_df.xlsx")
#Delhi_venues_df.to_excel("Delhi_venues_df.xlsx")
#Bangalore_venues_df.to_excel("Bangalore_venues_df.xlsx")
#Ahmedabad_venues_df.to_excel("Ahmedabad_venues_df.xlsx")
#Kolkata_venues_df.to_excel("Kolkata_venues_df.xlsx")
#Hyderabad_venues_df.to_excel("Hyderabad_venues_df.xlsx")

In [158]:
#District_rejected_list = Kolkata_rejected_list + Ahmedabad_rejected_list + Hyderabad_rejected_list + Bangalore_rejected_list + Mumbai_rejected_list + Delhi_rejected_list
#District_rejected_list_df = pd.DataFrame(District_rejected_list)
#District_rejected_list_df.to_excel("District_rejected_list_df.xlsx")

In [179]:
#District_venue_df = Mumbai_venues_df
#District_venue_df = District_venue_df.append(Delhi_venues_df, ignore_index= True, sort = False)
#District_venue_df = District_venue_df.append(Bangalore_venues_df, ignore_index= True, sort = False)
#District_venue_df = District_venue_df.append(Hyderabad_venues_df, ignore_index= True, sort = False)
#District_venue_df = District_venue_df.append(Ahmedabad_venues_df, ignore_index= True, sort = False)
#District_venue_df = District_venue_df.append(Kolkata_venues_df, ignore_index= True, sort = False)

In [183]:
#District_venue_df.to_excel("District_venue_df.xlsx")

In [189]:
District_venue_df.groupby('Area').count().head()

District  Area Latitude  Area Longitude  Venue  \
Area                                                               
505 A b workshop         4              4               4      4   
A F palam                3              3               3      3   
A F rajokari             3              3               3      3   
A I staff colony         8              8               8      8   
A-3 Janak puri           2              2               2      2   

                  Venue Latitude  Venue Longitude  Venue Category  
Area                                                               
505 A b workshop               4                4               4  
A F palam                      3                3               3  
A F rajokari                   3                3               3  
A I staff colony               8                8               8  
A-3 Janak puri                 2                2               2

In [193]:
# one hot encoding
district_onehot = pd.get_dummies(District_venue_df[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
district_onehot['Area'] = District_venue_df['Area'] 

# move neighborhood column to the first column
fixed_columns = [district_onehot.columns[-1]] + list(district_onehot.columns[:-1])
district_onehot = district_onehot[fixed_columns]

print(district_onehot.shape)
district_onehot.head()

(11934, 348)


Area  ATM  Accessories Store  Afghan Restaurant  Airport  \
0  A I staff colony    0                  0                  0        0   
1  A I staff colony    0                  0                  0        0   
2  A I staff colony    0                  0                  0        0   
3  A I staff colony    0                  0                  0        0   
4  A I staff colony    0                  0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Andhra Restaurant  Antique Shop  Aquarium  Arcade  \
0                    0                  0             0         0       0   
1                    0                  0             0         0       0   
2                    0                  0             0         0       0   
3                    0                  0             0         0       0   
4                    0                  0             0         0       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Astrologer  Athletics & Sports  Auto Garage  \
0                 0           0                   0            0   
1                 0           0                   0            0   
2                 0           0                   0            0   
3                 0           0                   0            0   
4                 1           0                   0            0   

   Auto Workshop  Automotive Shop  Awadhi Restaurant  BBQ Joint  Baby Store  \
0              0                0                  0          0           0   
1              0                0                  0          0           0   
2              0                0                  0          0           0   
3              0                0                  0          0           0   
4              0                0                  0          0           0   

   Badminton Court  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0                0           0       0     0    0               0   
1                0           0       0     0    0               0   
2                0           0       0     0    0               0   
3                0           0       0     0    0               0   
4                0           0       0     0    0               0   

   Basketball Court  Beach  Beach Bar  Bed & Breakfast  Beer Garden  \
0                 0      0          0                0            0   
1                 0      0          0                0            0   
2                 0      0          0                0            0   
3                 0      0          0                0            0   
4                 0      0          0                0            0   

   Bengali Restaurant  Bike Shop  Bistro  Boarding House  Boat or Ferry  \
0                   0          0       0               0              0   
1                   0          0       0               0              0   
2                   0          0       0               0              0   
3                   0          0       0               0              0   
4                   0          0       0               0              0   

   Bookstore  Boutique  Bowl

In [194]:
district_grouped = district_onehot.groupby('Area').mean().reset_index()

print(district_grouped.shape)
district_grouped.head()

(1401, 348)


Area  ATM  Accessories Store  Afghan Restaurant  Airport  \
0  505 A b workshop  0.0                0.0                0.0      0.0   
1         A F palam  0.0                0.0                0.0      0.0   
2      A F rajokari  0.0                0.0                0.0      0.0   
3  A I staff colony  0.0                0.0                0.0      0.0   
4    A-3 Janak puri  0.0                0.0                0.0      0.0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                 0.0             0.0              0.0               0.0   
1                 0.0             0.0              0.0               0.0   
2                 0.0             0.0              0.0               0.0   
3                 0.0             0.0              0.0               0.0   
4                 0.0             0.0              0.0               0.0   

   American Restaurant  Andhra Restaurant  Antique Shop  Aquarium  Arcade  \
0                  0.0                0.0           0.0       0.0     0.0   
1                  0.0                0.0           0.0       0.0     0.0   
2                  0.0                0.0           0.0       0.0     0.0   
3                  0.0                0.0           0.0       0.0     0.0   
4                  0.0                0.0           0.0       0.0     0.0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0          0.0         0.0                  0.0                   0.0   
1          0.0         0.0                  0.0                   0.0   
2          0.0         0.0                  0.0                   0.0   
3          0.0         0.0                  0.0                   0.0   
4          0.0         0.0                  0.0                   0.0   

   Asian Restaurant  Astrologer  Athletics & Sports  Auto Garage  \
0             0.000        0.25                 0.0          0.0   
1             0.000        0.00                 0.0          0.0   
2             0.000        0.00                 0.0          0.0   
3             0.125        0.00                 0.0          0.0   
4             0.000        0.00                 0.0          0.0   

   Auto Workshop  Automotive Shop  Awadhi Restaurant  BBQ Joint  Baby Store  \
0            0.0              0.0                0.0        0.0         0.0   
1            0.0              0.0                0.0        0.0         0.0   
2            0.0              0.0                0.0        0.0         0.0   
3            0.0              0.0                0.0        0.0         0.0   
4            0.0              0.0                0.0        0.0         0.0   

   Badminton Court  Bagel Shop  Bakery  Bank       Bar  Baseball Field  \
0              0.0         0.0     0.0   0.0  0.000000             0.0   
1              0.0         0.0     0.0   0.0  0.333333             0.0   
2              0.0         0.0     0.0   0.0  0.000000             0.0   
3              0.0         0.0     0.0   0.0  0.000000             0.0   
4              0.0         0.0     0.0   0.0  0.000000             0.0   

   Basketball Court  Beach  Beach Bar  Bed & Breakfast  Beer Garden  \
0               0.0    0.0        0.0              0.0          0.0   
1               0.0    0.0        0.0              0.0          0.0   
2               0.0    0.0        0.0              0.0          0.0   
3               0.0    0.0        0.0              0.0          0.0   
4               0.0    0.0        0.0              0.0          0.0   

   Bengali Restaurant  Bike Shop  Bistro  Boarding House  Boat or Ferry  \
0                 0.0        0.0     0.0             0.0            0.0   
1                 0.0        0.0     0.0             0.0            0.0   
2                 0.0        0.0     0.0             0.0            0.0   
3                 0.0        0.0     0.0             0.0            0.0   
4                 0.0        0.0     0.0             0.0            0.0   

In [195]:
num_top_venues = 5

for hood in district_grouped['Area']:
    print("----"+hood+"----")
    temp = district_grouped[district_grouped['Area'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----505 A b workshop----
                         venue  freq
0                  IT Services  0.25
1                   Astrologer  0.25
2               Discount Store  0.25
3         Fast Food Restaurant  0.25
4  Northeast Indian Restaurant  0.00


----A F palam----
               venue  freq
0  Mobile Phone Shop  0.33
1                Bar  0.33
2  Indian Restaurant  0.33
3                ATM  0.00
4  Other Repair Shop  0.00


----A F rajokari----
                  venue  freq
0  Gym / Fitness Center  0.33
1      Business Service  0.33
2                   Gym  0.33
3       Other Nightlife  0.00
4  Other Great Outdoors  0.00


----A I staff colony----
                    venue  freq
0                    Café  0.12
1  Furniture / Home Store  0.12
2                     Spa  0.12
3                Tea Room  0.12
4       Indian Restaurant  0.12


----A-3 Janak puri----
               venue  freq
0   Business Service   0.5
1         Restaurant   0.5
2                ATM   0.0
3  Other Repair 

                  venue  freq
0           IT Services   1.0
1                Palace   0.0
2     Other Repair Shop   0.0
3       Other Nightlife   0.0
4  Other Great Outdoors   0.0


----Anekal----
                     venue  freq
0                      ATM  0.67
1             Camera Store  0.33
2  North Indian Restaurant  0.00
3        Other Repair Shop  0.00
4          Other Nightlife  0.00


----Anekalbazar----
                  venue  freq
0                   ATM  0.67
1      Business Service  0.33
2     Other Repair Shop  0.00
3       Other Nightlife  0.00
4  Other Great Outdoors  0.00


----Aniali ( k )----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0.00


----Aniali Bhimji----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0

                  venue  freq
0                   ATM   1.0
1          Noodle House   0.0
2     Other Repair Shop   0.0
3       Other Nightlife   0.0
4  Other Great Outdoors   0.0


----Balapur----
               venue  freq
0                Bar   1.0
1                ATM   0.0
2      Moving Target   0.0
3  Other Repair Shop   0.0
4    Other Nightlife   0.0


----Balbir Nagar----
               venue  freq
0  Indian Restaurant   1.0
1                ATM   0.0
2       Noodle House   0.0
3  Other Repair Shop   0.0
4    Other Nightlife   0.0


----Balepete----
                  venue  freq
0     Indian Restaurant  0.19
1  Fast Food Restaurant  0.19
2           Bus Station  0.12
3                Bakery  0.06
4             Juice Bar  0.06


----Ballygunge----
              venue  freq
0          Boutique   0.2
1       Men's Store   0.2
2     Train Station   0.2
3  Business Service   0.2
4          Pharmacy   0.2


----Ballygunge Rs----
                           venue  freq
0             Ch

4                         Bakery  0.06


----Bengali Market----
               venue  freq
0  Indian Restaurant  0.23
1             Bakery  0.15
2               Café  0.15
3            Theater  0.15
4        Art Gallery  0.08


----Benson Town----
         venue  freq
0         Café  0.25
1       Bakery  0.25
2          Bar  0.25
3  Candy Store  0.25
4       Palace  0.00


----Best Staff colony----
                 venue  freq
0                 Café  0.29
1       Clothing Store  0.29
2     Asian Restaurant  0.14
3  Dumpling Restaurant  0.14
4    Mobile Phone Shop  0.14


----Bestamaranahalli----
                  venue  freq
0                   ATM  0.67
1      Business Service  0.33
2     Other Repair Shop  0.00
3       Other Nightlife  0.00
4  Other Great Outdoors  0.00


----Bettahalsur----
                         venue  freq
0            Indian Restaurant  0.50
1                         Lake  0.25
2                  Coffee Shop  0.25
3                          ATM  0.00
4  Northea

4     Shop & Service  0.11


----Cahmrajendrapet----
                venue  freq
0  Italian Restaurant  0.08
1                Café  0.08
2              Lounge  0.06
3  Mexican Restaurant  0.06
4               Hotel  0.04


----Calico Mills----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0.00


----Cantonment----
         venue  freq
0         Park  0.25
1        River  0.25
2  Art Gallery  0.25
3       Castle  0.25
4  Music Venue  0.00


----Central Building----
               venue  freq
0  Indian Restaurant  0.25
1               Café  0.17
2      Jewelry Store  0.17
3                Bar  0.08
4      Train Station  0.08


----Central Police lines----
              venue  freq
0    Cricket Ground  0.33
1  Kebab Restaurant  0.33
2          Tea Room  0.33
3               ATM  0.00
4      Noodle House  0.00


----Central Secretariat----
                 venue 

...

               venue  freq
0      Train Station   1.0
1                ATM   0.0
2             Palace   0.0
3  Other Repair Shop   0.0
4    Other Nightlife   0.0


----Shahwadi----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0.00


----Shakarpur----
           venue  freq
0            Gym  0.14
1    Snack Place  0.14
2          Diner  0.14
3  Train Station  0.14
4  Shopping Mall  0.14


----Shakespeare Sarani----
                venue  freq
0                Café  0.43
1  Mughlai Restaurant  0.14
2      Ice Cream Shop  0.07
3           Nightclub  0.07
4              Bakery  0.07


----Shakti Nagar----
                 venue  freq
0  Fried Chicken Joint  0.25
1         Concert Hall  0.25
2           Playground  0.25
3                 Café  0.25
4                  ATM  0.00


----Shakur Basti depot----
               venue  freq
0   Business Service   0.5
1   

                       venue  freq
0                       Café  0.12
1                     Bakery  0.12
2   Mediterranean Restaurant  0.04
3  Middle Eastern Restaurant  0.04
4            Thai Restaurant  0.04


----State Bank of mysore colony----
                  venue  freq
0     Indian Restaurant  0.19
1  Fast Food Restaurant  0.19
2           Bus Station  0.12
3                Bakery  0.06
4             Juice Bar  0.06


----Station Road----
                         venue  freq
0                  IT Services  0.25
1                   Astrologer  0.25
2               Discount Store  0.25
3         Fast Food Restaurant  0.25
4  Northeast Indian Restaurant  0.00


----Stn Kachiguda----
           venue  freq
0  Women's Store   0.2
1  Movie Theater   0.2
2           Bank   0.2
3    Coffee Shop   0.2
4    Snack Place   0.2


----Stock Exchange----
                        venue  freq
0  Tourist Information Center   0.5
1            Business Service   0.5
2                         ATM   

               venue  freq
0         Food Court   0.2
1              Hotel   0.2
2  Indian Restaurant   0.2
3        Pizza Place   0.2
4               Café   0.2


----Tollygunge----
                venue  freq
0              Lounge   0.2
1  Chinese Restaurant   0.2
2       Movie Theater   0.2
3              Bistro   0.2
4                Café   0.2


----Town Hall----
             venue  freq
0             Café  0.19
1       Public Art  0.06
2           Hostel  0.05
3       Food Truck  0.05
4  Bed & Breakfast  0.04


----Training Command iaf----
               venue  freq
0       Home Service   1.0
1                ATM   0.0
2             Palace   0.0
3  Other Repair Shop   0.0
4    Other Nightlife   0.0


----Transad----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0.00


----Trilok Puri----
                     venue  freq
0               Public Art  0.33


            venue  freq
0  Ice Cream Shop   0.2
1            Café   0.2
2      Playground   0.1
3          Bakery   0.1
4      Food Stand   0.1


----Venkateshapura----
               venue  freq
0                ATM   0.5
1          Pet Store   0.5
2             Palace   0.0
3  Other Repair Shop   0.0
4    Other Nightlife   0.0


----Vesava----
                venue  freq
0                Café  0.13
1   Indian Restaurant  0.11
2        Dessert Shop  0.05
3         Coffee Shop  0.05
4  Chinese Restaurant  0.05


----Vidhan Sabha----
                        venue  freq
0  Tourist Information Center   0.2
1                 Music Venue   0.2
2     Health & Beauty Service   0.2
3            Business Service   0.2
4                   Beach Bar   0.2


----Vidhana Soudha----
                        venue  freq
0  Tourist Information Center  0.17
1                      Garden  0.17
2            Capitol Building  0.17
3                       Hotel  0.17
4                    Vineyard  0.17


--

         venue  freq
0          ATM   0.2
1  Coffee Shop   0.2
2  Bus Station   0.2
3        Hotel   0.2
4         Park   0.2


----Yozna Vihar----
                     venue  freq
0        Accessories Store  0.33
1             Home Service  0.33
2              Film Studio  0.33
3                      ATM  0.00
4  North Indian Restaurant  0.00


----Zakir Nagar----
                     venue  freq
0                      ATM  0.25
1  Health & Beauty Service  0.25
2              IT Services  0.25
3            Jewelry Store  0.25
4                Wine Shop  0.00


----Zamistanpur----
                     venue  freq
0               Food Truck  0.25
1            Movie Theater  0.25
2        Convenience Store  0.25
3                   Hostel  0.25
4  North Indian Restaurant  0.00


----Zanzarka----
                  venue  freq
0         Historic Site  0.50
1  Fast Food Restaurant  0.25
2           Snack Place  0.25
3    Mughlai Restaurant  0.00
4     Other Repair Shop  0.00


----Zezra----

In [196]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [197]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Area']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
area_venues_sorted = pd.DataFrame(columns=columns)
area_venues_sorted['Area'] = district_grouped['Area']

for ind in np.arange(district_grouped.shape[0]):
    area_venues_sorted.iloc[ind, 1:] = return_most_common_venues(district_grouped.iloc[ind, :], num_top_venues)

area_venues_sorted.head()

Area   1st Most Common Venue       2nd Most Common Venue  \
0  505 A b workshop    Fast Food Restaurant                  Astrologer   
1         A F palam       Indian Restaurant                         Bar   
2      A F rajokari        Business Service        Gym / Fitness Center   
3  A I staff colony  Furniture / Home Store  Modern European Restaurant   
4    A-3 Janak puri        Business Service                  Restaurant   

  3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0           IT Services           Discount Store                   Zoo   
1     Mobile Phone Shop                      Zoo     Food & Drink Shop   
2                   Gym  Fruit & Vegetable Store  Fast Food Restaurant   
3      Asian Restaurant                     Café           Coffee Shop   
4                   Zoo                     Farm  Fast Food Restaurant   

  6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
0                  Food                 Field                 Film Studio   
1                 Field           Film Studio  Financial or Legal Service   
2                 Field           Film Studio  Financial or Legal Service   
3              Tea Room     Indian Restaurant                         Spa   
4                 Field           Film Studio  Financial or Legal Service   

        9th Most Common Venue 10th Most Common Venue  
0  Financial or Legal Service            Fish Market  
1                 Fish Market            Flea Market  
2                 Fish Market            Flea Market  
3                      Forest      French Restaurant  
4                 Fish Market            Flea Market

In [232]:
# set number of clusters
kclusters = 5

district_grouped_clustering = district_grouped.drop('Area', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(district_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 0, 3, 3, 3, 0, 3, 3, 3, 3])

In [276]:
# add clustering labels
#area_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
print(Area_Loc_df.shape)
district_merged = Area_Loc_df
print(district_merged.shape)

# merge manhattan_grouped with manhattan_data to add latitude/longitude for each neighborhood
district_merged = district_merged.join(area_venues_sorted.set_index('Area'), on='Area')
print(district_merged.shape)
print(district_merged[district_merged['Cluster Labels'].isnull()])
district_merged['Cluster Labels'] = pd.to_numeric(district_merged['Cluster Labels'], errors='coerce')
district_merged = district_merged.dropna(subset=['Cluster Labels'])
district_merged['Cluster Labels'] = district_merged['Cluster Labels'].astype(int)

print(district_merged.head()) # check the last columns!

(1913, 6)
(1913, 6)
(1913, 17)
                               Area          District        State Pincode  \
9                            Asvini            Mumbai  Maharashtra  400005   
19                     Bharat Nagar            Mumbai  Maharashtra  400007   
24                     Borvali West            Mumbai  Maharashtra  400092   
25                     C G s colony            Mumbai  Maharashtra  400013   
112                    Mazgaon Dock            Mumbai  Maharashtra  400010   
166                      V K bhavan            Mumbai  Maharashtra  400010   
240                     Anand Vihar        East Delhi        Delhi  110092   
248                        Dayalpur        East Delhi        Delhi  110094   
257                      Gokal Puri        East Delhi        Delhi  110094   
261                        Jafrabad        East Delhi        Delhi  110053   
265                        Johripur        East Delhi        Delhi  110094   
269                   Karawal Nag

In [277]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=4)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(district_merged['Latitude'], district_merged['Longitude'], district_merged['Area'], district_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster) - 1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters